In [ ]:
# !pip install transformers
# !pip install tokenizers
!pip install --upgrade accelerate

In [2]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, GPT2Config
from transformers import TextDataset, DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments

In [3]:
# load the pre trained model
#currently got the GPT 2 (Base model) working
model_name = 'gpt2' # https://huggingface.co/openai-community/gpt2
model = GPT2LMHeadModel.from_pretrained(model_name)
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
config = GPT2Config.from_pretrained(model_name)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [4]:
# testing without finetuning base model
input_text = 'Hello how are you?'
input_ids = tokenizer.encode(input_text, return_tensors='pt')

output = model.generate(input_ids, max_length=100, num_return_sequences=1, no_repeat_ngram_size=2)
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print(generated_text)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token.As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Hello how are you?

I'm a little bit of a nerd. I'm not a big fan of the show, but I've been watching it for a while now and I think it's a great show. It's funny, it has a lot of great characters, and it does a good job of making you feel like you're part of something bigger than yourself.
...
 (Laughs.)



What's your favorite part about the series?

.




In [8]:
# download book by the author.
# In our case students might filter the gutenberg library to get books by their favourite author and train the model to answer in
# the authors tone

# Sample books -for testing
#!wget https://raw.githubusercontent.com/brunoklein99/deep-learning-notes/master/shakespeare.txt -O shakespeare.txt

# All shakespeare books
!wget https://gist.githubusercontent.com/blakesanie/dde3a2b7e698f52f389532b4b52bc254/raw/76fe1b5e9efcf0d2afdfd78b0bfaa737ad0a67d3/shakespeare.txt -O shakespeare.txt

--2024-08-31 05:45:45--  https://gist.githubusercontent.com/blakesanie/dde3a2b7e698f52f389532b4b52bc254/raw/76fe1b5e9efcf0d2afdfd78b0bfaa737ad0a67d3/shakespeare.txt
Resolving gist.githubusercontent.com (gist.githubusercontent.com)... 185.199.110.133, 185.199.108.133, 185.199.111.133, ...
Connecting to gist.githubusercontent.com (gist.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 5436475 (5.2M) [text/plain]
Saving to: ‘shakespeare.txt’

shakespeare.txt     100%[===================>]   5.18M  --.-KB/s    in 0.07s   

2024-08-31 05:45:45 (79.1 MB/s) - ‘shakespeare.txt’ saved [5436475/5436475]



In [13]:
# prepare the dataset

train_path = 'shakespeare.txt'
train_dataset = TextDataset(
    tokenizer=tokenizer,
    file_path=train_path,
    block_size=128
)

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer,
    mlm=False
)

/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [14]:
# set up training args
training_args = TrainingArguments(
    output_dir='./results',
    overwrite_output_dir=True,
    num_train_epochs=3,
    per_device_eval_batch_size=32,
    eval_steps=100,
    save_steps=10_000,
    warmup_steps=500,
)

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
)

In [15]:
trainer.train()

TrainOutput(global_step=75, training_loss=4.883878580729166, metrics={'train_runtime': 32.7918, 'train_samples_per_second': 18.023, 'train_steps_per_second': 2.287, 'total_flos': 38605897728000.0, 'train_loss': 4.883878580729166, 'epoch': 3.0})

In [16]:
output_dir = './results'
model.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

('./results/tokenizer_config.json',
 './results/special_tokens_map.json',
 './results/vocab.json',
 './results/merges.txt',
 './results/added_tokens.json')

In [17]:
del model
del tokenizer

In [18]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer

# Loading the new model from local dir
output_dir = './results'
model = GPT2LMHeadModel.from_pretrained(output_dir)
tokenizer = GPT2Tokenizer.from_pretrained(output_dir)

In [19]:
#Testing the new model
input_text = 'Hello how are you?'
input_ids = tokenizer.encode(input_text, return_tensors='pt')

output = model.generate(input_ids, max_length=100, num_return_sequences=1, no_repeat_ngram_size=2)
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

print(generated_text)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Hello how are you?

I am a man of the world,
And I am not a woman, but a child.
But I have a wife, and a son, who is my own.


What do you say, my dear, that I should not be so kind to you, when I love you so much?




